In [4]:
import sys
sys.executable

'/home/goonieb/anaconda2/bin/python'

In [5]:
import os
import json
import pymongo
import musicbrainzngs
import arrow
from datetime import datetime
from pymongo import MongoClient
from collections import defaultdict
from dateutil import parser
import pickle


In [ ]:
# setup mongo
client = MongoClient()
db = client["bandstour"]
bandsintown =  db["bandsintown"]



#setup mbrainz client
musicbrainzngs.set_useragent("Example music app", "0.1", "http://example.com/music")

# source data
DATA_FOLDER = "data/labels"
countMBID = 0
countNAME = 0
count = 0
# date parsing
DATETIME_FORMAT = '%Y-%m-%dT%H:%M:%S'
DATETIME_FORMAT_FOR_MSBNZ ='%Y-%m-%d'
# init label_db_retrieval
labels_aliases ={}
#retrieve label for each artist before a tour starts
#i.e what is the album previously to the first year
for artist in db.minedArtists.find() :
                    print artist["name"]
    
                    #print db.minedArtists[artist]
                    #print artist
                    labels_dict= defaultdict(list)
                    labels_dict["id"]=[]

                    if  artist["mbid"] is ( None ) :
                        print ("NOMBID for",artist["name"])

                    else:
                     if  bool(artist["mbid"]) is ( False ) :
                      print ("NOMBID2 for",artist["name"])

                     else:
                      print "aartist_mbid", artist["mbid"]
                     if os.path.exists("./release_mbnz/"+artist["name"]+artist["mbid"]+".obj")==True:
                      with open("./release_mbnz/"+artist["name"]+artist["mbid"]+".obj", 'rb') as handle:
                        artist["releases"]= pickle.load(handle)
                     else:
                      try:
                        artist["releases"]=(musicbrainzngs.browse_releases( artist["mbid"], release_type=["album"], includes=["labels"] ))
                        try:
                            with open("./release_mbnz/"+artist["name"]+artist["mbid"]+".obj", 'wb') as handle:
                                pickle.dump(artist["releases"], handle, protocol=pickle.HIGHEST_PROTOCOL)    
                        except:
                            pass
                        #print "...."
                        #print artist["release_groups"]
                        key= 0
                        for release in  artist["releases"]["release-list"]:
                            #print release
                            if  release.has_key("release-event-list"):
                                #print "artist_name:",artist["name"]
                                #print "albumtitle:",release["title"]
                                #print "albumid:",release["id"]
                                #print "label-list",release["label-info-list"]
                                #print "releaseLBL",release["label-info-list"]
                                if not release["label-info-list"]:
                                    print "pppppppppppppp"
                                
                                else:
                                 if release["label-info-list"][0].has_key('label'):
                                  for label in release["label-info-list"]:
                                    #WE NEED TO TEST HERE
                                    #print "label:",label["label"]["sort-name"]
                                    #print "labelid:",label
                                    
#WE CREATE A DICTIONNARY WITH OUR FIELDS, WITH FORMAT
                                    if label.has_key('label'):
                                     if label["label"]["id"] not in labels_dict["labids"]:
                                        labels_dict["labids"].append(label["label"]["id"])
                                        labels_dict[label["label"]["id"]]={}

                                        labels_dict[label["label"]["id"]]["label_name"]=label["label"]["sort-name"]
                                        labels_dict[label["label"]["id"]]["label_id" ]=label["label"]["id"]
#WE Build the label aliases tables here so that all labels have their relationships##
                                        if label["label"]["id"] not in labels_aliases:
                                            labels_aliases[label["label"]["id"]] = musicbrainzngs.get_label_by_id(label["label"]["id"], includes=["aliases", "annotation", "area-rels", "label-rels", "place-rels"])
                                        #print "labels_aliases",labels_aliases
                                     labels_dict[label["label"]["id"]][str(key)]={}
                                    #print key
                                     labels_dict[label["label"]["id"]][str(key)]["album_id"]=release["id"]
                                     labels_dict[label["label"]["id"]][str(key)]["album_title"]=release["title"]
                                     releDate=release["release-event-list"][0]
                                #print "releDate", release["release-event-list"][0]
                                     if  releDate.has_key("date"):
                                        dateRel=arrow.get(releDate["date"])
                                        #print "date:", dateRel.strftime('%Y-%m-%d')
                                        labels_dict[label["label"]["id"]][str(key)]["album_date"]=dateRel.strftime('%Y-%m-%d')
                                     key = key +1
                                 else:
                                    print "NORELEASEDATE2"
                                    #key = key +1
                            #else:
                                #key = key +1
                                #print "NORELEASEDATE"
#NOW we make a nice lightweight object to push to mongo
                        labels_dict["name"]=artist["name"]
                        print labels_dict["name"],'\r\n'
                        db.labels_dict_per_artist.update({'myid': artist["name"] } ,labels_dict, upsert=True, multi=False)
                      except  musicbrainzngs.ResponseError:
                        print "oups",artist["name"]

                #with open(os.path.join(DATA_FOLDER,artist["name"],".json"), 'w') as outfile:
                             #   json.dump(labels_dict, outfile)
                            #db.minedArtists.artist.insert_one(labels_dict)
#with open(os.path.join(DATA_FOLDER,"label_equiv_table.json"), 'w') as outfile:
 #                               json.dump(labels_aliases, outfile)
#print labels_aliases,'\r\n\r\n\r\n'
import pickle



with open('labels_aliases.obj', 'wb') as handle:
    pickle.dump(labels_aliases, handle, protocol=pickle.HIGHEST_PROTOCOL)



조수미
aartist_mbid dd21a142-cf44-4e22-add6-a50eea696854
Лили Иванова
aartist_mbid ab634a19-20e3-4801-975e-a230f899af8a
ᵀᴴᴱ ᴼᴿᴵᴳᴵᴻᴬᴸ Funky Monkey
('NOMBID for', u'\u1d40\u1d34\u1d31 \u1d3c\u1d3f\u1d35\u1d33\u1d35\u1d3b\u1d2c\u1d38 Funky Monkey')
Калевала
('NOMBID for', u'\u041a\u0430\u043b\u0435\u0432\u0430\u043b\u0430')
Кристина Орбакайте
aartist_mbid e71738bd-39d4-4699-b6c2-688f95b31732
Дмитрий Дмитриевич Шостакович
aartist_mbid 519dd32e-8f30-4380-8826-7aa99169e1bb
Валерия
aartist_mbid b4313680-2f57-4ec6-87a7-24873133ba4c
Евгений Игоревич Кисин
aartist_mbid 5761282a-0965-4ff6-9796-7b9ba0ed70e2
Би-2
aartist_mbid 5ca35ace-4006-4d4a-af04-5cd91dafab14
Анна Юрьевна Нетребко
aartist_mbid 90cba256-80b2-464f-9d58-a877a3757d3a
Μελίνα Ασλανίδου
aartist_mbid d55702f8-1b33-494e-8c9c-e6fd948bbee8
ŚexPistols Eẋperience
('NOMBID for', u'\u015aexPistols E\u1e8bperience')
ÜBERMENSCH (Rammstein Tribute Band)
('NOMBID for', u'\xdcBERMENSCH (Rammstein Tribute Band)')
Ørsted
('NOMBID for', u'\xd8rsted')
Øka

truett
('NOMBID for', u'truett')
transient
aartist_mbid 4cb5b170-07f9-4428-bdfa-7b74a2122553
tori kelly
('NOMBID for', u'tori kelly')
tobyMac
aartist_mbid 8484e4ab-b6b5-4326-b837-72eb72c9e8a4
tim gearan
('NOMBID for', u'tim gearan')
theo kottis
('NOMBID for', u'theo kottis')
theSHIFT
('NOMBID for', u'theSHIFT')
the vaughns
('NOMBID for', u'the vaughns')
the the Band Band
('NOMBID for', u'the the Band Band')
the peptides
('NOMBID for', u'the peptides')
the magician
('NOMBID for', u'the magician')
the Workshy
('NOMBID for', u'the Workshy')
the Whooligan
('NOMBID for', u'the Whooligan')
the Way Up
('NOMBID for', u'the Way Up')
the ThoughtCriminals
('NOMBID for', u'the ThoughtCriminals')
the Tea Club
('NOMBID for', u'the Tea Club')
the Stuntmen
('NOMBID for', u'the Stuntmen')
the Stampede
('NOMBID for', u'the Stampede')
the Sour Notes
('NOMBID for', u'the Sour Notes')
the Snips
('NOMBID for', u'the Snips')
the Sleeper
('NOMBID for', u'the Sleeper')
the Ruination
('NOMBID for', u'the Ruinat

oups yellowtieguy
xxyyxx
('NOMBID for', u'xxyyxx')
www.kierangoss.com
('NOMBID for', u'www.kierangoss.com')
wonder woman
('NOMBID for', u'wonder woman')
william becket
('NOMBID for', u'william becket')
whetherman
('NOMBID for', u'whetherman')
wax wings
('NOMBID for', u'wax wings')
w/Billy Masters on guitar
('NOMBID for', u'w/Billy Masters on guitar')
w/ This Or The Apocalypse, Ice Nine Kills
('NOMBID for', u'w/ This Or The Apocalypse, Ice Nine Kills')
w/ For Today, The Word Alive, Memphis May Fire, and Upon A Burning Body  
('NOMBID for', u'w/ For Today, The Word Alive, Memphis May Fire, and Upon A Burning Body  ')
vverevvolf
('NOMBID for', u'vverevvolf')
viech
('NOMBID for', u'viech')
uvm.
('NOMBID for', u'uvm.')
tyler boone
('NOMBID for', u'tyler boone')
trp
('NOMBID for', u'trp')
theSurrendering
('NOMBID for', u'theSurrendering')
the kats
('NOMBID for', u'the kats')
the come up
('NOMBID for', u'the come up')
the black sound
('NOMBID for', u'the black sound')
the World's Hottest '80s

oups many
mafia rusa
('NOMBID for', u'mafia rusa')
lucent dossier
('NOMBID for', u'lucent dossier')
litz 
('NOMBID for', u'litz ')
linnie & amy joy
('NOMBID for', u'linnie & amy joy')
lilabungalow
('NOMBID for', u'lilabungalow')
laCasta
('NOMBID for', u'laCasta')
la Rappresentante di Lista
('NOMBID for', u'la Rappresentante di Lista')
kojey radical
('NOMBID for', u'kojey radical')
kirk baxley
('NOMBID for', u'kirk baxley')
kachupa
('NOMBID for', u'kachupa')
k.flay
aartist_mbid d1fc999f-6184-41a6-bcb1-7c59bf74a6e1
joe mullins
('NOMBID for', u'joe mullins')
joe fox
('NOMBID for', u'joe fox')
jason philips
('NOMBID for', u'jason philips')
iwrestledabearonce, Oceano, For All Those Sleeping
('NOMBID for', u'iwrestledabearonce, Oceano, For All Those Sleeping')
it's always sunny in tijuana
('NOMBID for', u"it's always sunny in tijuana")
ici et lui
('NOMBID for', u'ici et lui')
iAROSS
('NOMBID for', u'iAROSS')
honey mustard
('NOMBID for', u'honey mustard')
hold youth
('NOMBID for', u'hold yout

Yours Tour
('NOMBID for', u'Yours Tour')
Youngstar
aartist_mbid 3e4b368a-883d-4aa3-a72f-06b938b89862
Young's Modulus
('NOMBID for', u"Young's Modulus")
Young and in the Way
('NOMBID for', u'Young and in the Way')
Young Valley
('NOMBID for', u'Young Valley')
Young Rising Sons
('NOMBID for', u'Young Rising Sons')
Young Nudy
('NOMBID for', u'Young Nudy')
Young Marco
('NOMBID for', u'Young Marco')
Young Lions
aartist_mbid b8908707-2426-4c19-bf6c-ecc87865176c
Young Frankenstein
('NOMBID for', u'Young Frankenstein')
Young Distractions
('NOMBID for', u'Young Distractions')
Young Culture
('NOMBID for', u'Young Culture')
Young Cardinals
('NOMBID for', u'Young Cardinals')
Younee
('NOMBID for', u'Younee')
You're a Good Man Charlie Brown
('NOMBID for', u"You're a Good Man Charlie Brown")
You The Few
('NOMBID for', u'You The Few')
You Man
('NOMBID for', u'You Man')
You Blew It!
('NOMBID for', u'You Blew It!')
Yotam Ben Horin
('NOMBID for', u'Yotam Ben Horin')
Yonder Mountain String Band
aartist_mbi

...

Alex Kidd 

Alabama Mike
('NOMBID for', u'Alabama Mike')
Alex Diaz
('NOMBID for', u'Alex Diaz')
Al Di Meola
aartist_mbid 09c0f334-f9de-4970-b9ee-ef799cd093be
pppppppppppppp
Al Di Meola 

Alex Aiono
('NOMBID for', u'Alex Aiono')
Alesana
aartist_mbid 1079b087-a5b3-4a07-abbc-88043ceda334
Alesana 

Akilavue
('NOMBID for', u'Akilavue')
Alden
('NOMBID for', u'Alden')
Ajhenda
('NOMBID for', u'Ajhenda')
Akala
aartist_mbid 315856f7-2f28-4fb7-b2ac-cc019749da1d
NORELEASEDATE2
Akala 

Airlooms
('NOMBID for', u'Airlooms')
Aine Duffy
('NOMBID for', u'Aine Duffy')
Aja
aartist_mbid 3a8d749f-c0af-463f-a612-8eeb53047d16
Aja 

Albert Hammond
aartist_mbid 364f3cef-442b-4182-ae78-4e7e79683c24
pppppppppppppp
pppppppppppppp
pppppppppppppp
NORELEASEDATE2
pppppppppppppp
Albert Hammond 

Airdice
('NOMBID for', u'Airdice')
Alastair Greene
aartist_mbid c0349a70-993d-45a1-a239-5ecfbaa71e02
Alastair Greene 

Aimee Mann
aartist_mbid db3c0a20-bf05-4b30-ac22-f294aea24172
pppppppppppppp
Aimee Mann 

Alan Castro
('NOMBI

pppppppppppppp
Adam Carolla 

Adil Hiani
('NOMBID for', u'Adil Hiani')
Ada
aartist_mbid 86bb09f3-7ace-45dc-b26a-6833b18ecb85
Ada 

Across the white water tower
('NOMBID for', u'Across the white water tower')
Acoustic Rooster
('NOMBID for', u'Acoustic Rooster')
Ackerman Music
('NOMBID for', u'Ackerman Music')
Air Dubai
aartist_mbid 872795ed-6f97-4b8e-a4c1-e922eed52da1
pppppppppppppp
pppppppppppppp
Air Dubai 

Ags Connolly
('NOMBID for', u'Ags Connolly')
Alaska
aartist_mbid 97ca683a-b201-4ef1-9d38-a827dd4e8d16
Alaska 

Agents Of Time
('NOMBID for', u'Agents Of Time')
Alan Walker
('NOMBID for', u'Alan Walker')
Airlift NYC
('NOMBID for', u'Airlift NYC')
Alain Jean-Marie
('NOMBID for', u'Alain Jean-Marie')
Alabama Avenue
('NOMBID for', u'Alabama Avenue')
Ahmad Jamal
aartist_mbid cf816800-4e0e-4d80-9cca-50a725e93787
NORELEASEDATE2
Ahmad Jamal 

Akira
aartist_mbid 7dfab6ff-36e4-4b9b-b303-46c7dd4eb539
Akira 

Ajoyo
('NOMBID for', u'Ajoyo')
Aggravator
('NOMBID for', u'Aggravator')
Airplane Mode

Appleblim 

Acoustic Eidolon
aartist_mbid 6fe5a579-537f-4ae1-b80b-6719cbdfdd1a
pppppppppppppp
pppppppppppppp
pppppppppppppp
pppppppppppppp
Acoustic Eidolon 

Acera
('NOMBID for', u'Acera')
Apathy Wizards
('NOMBID for', u'Apathy Wizards')
Accentus
('NOMBID for', u'Accentus')
Antonio Sánchez & Migration
('NOMBID for', u'Antonio S\xe1nchez & Migration')
Action Bronson
('NOMBID for', u'Action Bronson')
Absolute Suffering
('NOMBID for', u'Absolute Suffering')
Antoine V
('NOMBID for', u'Antoine V')
Acropolis
('NOMBID for', u'Acropolis')
Antilles
aartist_mbid 9a344292-986f-4710-9551-e5d20b68fc24
Antilles 

Acoustic Duo
('NOMBID for', u'Acoustic Duo')
Airside
('NOMBID for', u'Airside')
Ahora
('NOMBID for', u'Ahora')
Aggressive Betty
('NOMBID for', u'Aggressive Betty')
Agathe Ze Bouse
('NOMBID for', u'Agathe Ze Bouse')
Above & Beyond
aartist_mbid 370bd5a3-4abf-4356-8576-3a8fc0c11d65
Above & Beyond 

Against All Odds
aartist_mbid a96a54ae-344b-4e68-a50b-e7243e30c10b
pppppppppppppp
Against All Od

Angela Strehli 

Anggun Cipta Sasmi
('NOMBID for', u'Anggun Cipta Sasmi')
Angel and Josh
('NOMBID for', u'Angel and Josh')
Angelica Robinson
('NOMBID for', u'Angelica Robinson')
AME
aartist_mbid f648fec6-59cf-4a46-b43c-bb2549d856f8
AME 

Andy Shaw Band
('NOMBID for', u'Andy Shaw Band')
Angela McCluskey
aartist_mbid 60b4dfdb-74fc-4d08-9b8b-b2c55fba33c1
pppppppppppppp
pppppppppppppp
Angela McCluskey 

Angel Snow
('NOMBID for', u'Angel Snow')
Andy Hamilton & the Whiskey Hitchers
('NOMBID for', u'Andy Hamilton & the Whiskey Hitchers')
Andy Cohen
('NOMBID for', u'Andy Cohen')
Andromeda
aartist_mbid 91200fcf-2aed-4f64-8c6d-801ab38c3e5d
Andromeda 

Andy Mineo
('NOMBID for', u'Andy Mineo')
Andrew Sapin
('NOMBID for', u'Andrew Sapin')
ALGEBRA BLESSETT
('NOMBID for', u'ALGEBRA BLESSETT')
ALAN JONES
('NOMBID for', u'ALAN JONES')
Andrew Calhoun
aartist_mbid cafd0394-fa10-4f69-8368-93b0756cf439
Andrew Calhoun 

Andy Fairweather Low & The Low Riders
('NOMBID for', u'Andy Fairweather Low & The Low Ri

Antisect 

AIR RAID
('NOMBID for', u'AIR RAID')
Antichrist
aartist_mbid f970182d-c157-4f8a-9259-444a7fd8440d
Antichrist 

ACKER
('NOMBID for', u'ACKER')
Anthony Manzo, bass
('NOMBID for', u'Anthony Manzo, bass')
Ages Apart
('NOMBID for', u'Ages Apart')
AfterShow
('NOMBID for', u'AfterShow')
Anthony D'Amato
('NOMBID for', u"Anthony D'Amato")
Abigail Washburn
aartist_mbid 545e6dac-993f-4841-8464-df0f5eadb7c2
Abigail Washburn 

Abigail
aartist_mbid e4c6d483-1cb0-4801-90f4-27637be2545c
Abigail 

Abdullah Ibrahim
aartist_mbid fd64e185-9973-44d5-ad09-5d5562804292
Abdullah Ibrahim 

Antarctic Monkeys
('NOMBID for', u'Antarctic Monkeys')
Anoxide
('NOMBID for', u'Anoxide')
Abbath -Official-
('NOMBID for', u'Abbath -Official-')
Annika
('NOMBID for', u'Annika')
Afroman
aartist_mbid 8c332797-2784-45a7-9b5c-3b86f07a03de
pppppppppppppp
pppppppppppppp
pppppppppppppp
pppppppppppppp
pppppppppppppp
pppppppppppppp
pppppppppppppp
pppppppppppppp
pppppppppppppp
pppppppppppppp
Afroman 

Aazar
('NOMBID for', 

In [ ]:
with open("labels_aliases.obj", 'rb') as handle:
                        labels_aliases= pickle.load(handle)

In [15]:
print str(labels_aliases)[:10000]

{'e39982c8-5d30-4cc0-bd2f-a878985a0706': {'label': {'name': 'Architecture', 'area': {'sort-name': 'Australia', 'iso-3166-1-code-list': ['AU'], 'id': '106e0bec-b638-3b37-b731-f53d507dc00e', 'name': 'Australia'}, 'country': 'AU', 'disambiguation': 'Australian', 'alias-count': 1, 'sort-name': 'Architecture', 'alias-list': [{'sort-name': 'Architecture label', 'alias': 'Architecture label'}], 'type': 'Original Production', 'id': 'e39982c8-5d30-4cc0-bd2f-a878985a0706'}}, '781c73fd-71d0-4309-b9bb-a3036ffc705c': {'label': {'name': 'The Spew Records', 'area': {'sort-name': 'Italy', 'iso-3166-1-code-list': ['IT'], 'id': 'c6500277-9a3d-349b-bf30-41afdbf42add', 'name': 'Italy'}, 'country': 'IT', 'life-span': {'begin': '2000'}, 'alias-count': 1, 'sort-name': 'The Spew Records', 'alias-list': [{'sort-name': 'Spew Records, The', 'alias': 'The Spew Records'}], 'type': 'Original Production', 'id': '781c73fd-71d0-4309-b9bb-a3036ffc705c'}}, 'a7d455f1-93f6-4bb7-a9cf-e4514efd7e02': {'label': {'sort-name': 

In [21]:
for lab in labels_aliases:
    print labels_aliases[lab]["label"]

{'name': 'Architecture', 'area': {'sort-name': 'Australia', 'iso-3166-1-code-list': ['AU'], 'id': '106e0bec-b638-3b37-b731-f53d507dc00e', 'name': 'Australia'}, 'country': 'AU', 'disambiguation': 'Australian', 'alias-count': 1, 'sort-name': 'Architecture', 'alias-list': [{'sort-name': 'Architecture label', 'alias': 'Architecture label'}], 'type': 'Original Production', 'id': 'e39982c8-5d30-4cc0-bd2f-a878985a0706'}
{'name': 'The Spew Records', 'area': {'sort-name': 'Italy', 'iso-3166-1-code-list': ['IT'], 'id': 'c6500277-9a3d-349b-bf30-41afdbf42add', 'name': 'Italy'}, 'country': 'IT', 'life-span': {'begin': '2000'}, 'alias-count': 1, 'sort-name': 'The Spew Records', 'alias-list': [{'sort-name': 'Spew Records, The', 'alias': 'The Spew Records'}], 'type': 'Original Production', 'id': '781c73fd-71d0-4309-b9bb-a3036ffc705c'}
{'sort-name': 'Ulftone Music', 'name': 'Ulftone Music', 'area': {'sort-name': 'Germany', 'iso-3166-1-code-list': ['DE'], 'id': '85752fda-13c4-31a3-bee5-0e5cb1f51dad', 'n

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.
